
## Planning with Equality

This is code for generating planning problems from "Planning with Equality" (David Plaisted, Stephan Schulz, 2024) in TPTP syntax. Most of the code is fairly harmless. However, the large "ground problems" from the switch domain will result in some very large output files and lead to a overall runtime for the script on the order of minutes. You can comment out the calls to "groundversion" below - all the rest should run in at most a few seconds.

Files will be created in the directory the notebook was started from.

For questions about this notebook, please contact Stephan Schulz, schulz@eprover.org.


In [1]:
import sys


### Flipping Switches

This is code for generating the simple switch problems from "Planning with Equality".

We assume a bank of switches, each of which can bei either "on" or "off. We are
looking for a plan (i.e. in our setting equational proof) converting the bank
from one arbitrary state to another arbitrary state. Currently, therer are two different start and 
goal states more or less hard-coded. One version has all switches with alternating on/off values, offset by one between inial and goal state, i.e. the plan must toggle all switches). The other version has all switches "on" in the inial state, all but the first "on" in the goal state. In other words, an optimal plan needs to switch only one single switch.

There are three different encoding. 
- The first allows only rewriting of the complete state and only ground rules. In other words, there is one rule for each action in each state. 
- The second encoding still requires rewriting of the full state, but allow variables to capture invariant parts. For this, we need two rules per switch, one to turn the switch on, one to turn it off. 
- The final encoding allows rewriting at subterm position, i.e. we need only a single rule to turn any switch on (and one to turn it off)
In the equational setting, all rules are invertible, i.e. we can usually express two symmetrical rules by one equa

In principle, we can generate problems of any size (though the ground version will
become unhandy very quickly.


In [2]:
def alternatingStates(n, s1, s2):
    return (",".join(([s1, s2]*n)[0:n]))
   
def tptpInit(n):
    return "cnf(to_plan, negated_conjecture, f(%s)!=f(%s))."%(alternatingStates(n, "on", "off"), alternatingStates(n, "off", "on"))

def tptpInit2(n):
    init = ["on"]*n
    goal = ["on"]*n
    goal[0] = "off"
    initstr = ",".join(init)
    goalstr = ",".join(goal)
    
    return "cnf(to_plan, negated_conjecture, f(%s)!=f(%s))."%(initstr,goalstr)

def makeVarlist(var, n):
    return ["%s%d"%(var,i) for i in range(n)]

def makeVarAxiomsI(n,i):
    varlist1 = makeVarlist("X", n)
    varlist2 = makeVarlist("X", n)
    varlist1[i] = "on"
    varlist2[i] = "off"
    ax1 = "cnf(n_%d_%d_off, axiom, f(%s) = f(%s))."%(n,i, ",".join(varlist1), ",".join(varlist2))
    ax2 = "cnf(n_%d_%d_on,  axiom, f(%s) = f(%s))."%(n,i, ",".join(varlist2), ",".join(varlist1))
    return [ax1, ax2]

def makeVarAxioms(n):
    res = []
    for i in range(n):
        res.extend(makeVarAxiomsI(n,i))
    return res

def makeTuples(n, tuples, values):
    if n==0:
        return tuples
    res = []
    for val in values:
        res.extend([[val]+x for x in makeTuples(n-1, tuples, values)])
    return res  

def flipNth(tuple, n):
    res = [x for x in tuple]
    if res[n]=="on":
        res[n]="off"
    else:
        res[n]="on"
    return res  

def makeGroundAx(tuple, n):
    axiom = "cnf(g_%d_%s, axiom, f(%s)=f(%s))."% \
        (n, "_".join(tuple), ",".join(tuple), ",".join(flipNth(tuple,n)))
    return axiom
    
def makeGroundAxioms(n):
    tuples = makeTuples(n, [[]], ["on", "off"])
    res = []
    for t in tuples:
        for i in range(n):
            res.append(makeGroundAx(t,i))
    return res



def groundVersion(n, init=tptpInit):
    print("""
%% Simple switchbank example. There are %d switches 
%% that can be on or off. Actions flip a single switch.
%%
%% This is the ground version.
%%
%% Each possible action in each possible state is encoded 
%% in one rule, i.e. we have 2^n*n=%d action rules.
"""%(n, (2**n)*n))
    print(init(n))
    g_axioms = makeGroundAxioms(n)
    print("\n".join(g_axioms))


def varVersion(n, init=tptpInit):
    print("""
%% Simple switchbank example. There are %d switches 
%% that can be on or off. Actions flip a single switch.
%%
%% This is the version using first-order variables. 
%% 
%% The states of non-relevant switches are captured (and 
%% preserved) by variables, so we only need one rule to
%% turn each switch on, and one to turn it off. Thus
%% we have 2n=%d action rules.
"""%(n, (2*n)))
    print(init(n))
    v_axioms = makeVarAxioms(n)
    print("\n".join(v_axioms))
    
    
def subtermVersion(n, init=tptpInit):
    print("""
%% Simple switchbank example. There are %d switches 
%% that can be on or off. Actions flip a single switch.
%%
%% This is the version using rewriting at subterm positions,
%% using a single action rule that can flip any switch.
%% 
%% There should be two axioms, on->off and off->on. However,
%% since we require bidirectionality, both are covered by a
%% single equation.
"""%(n))
    print(init(n))
    s_axiom = "cnf(onoff,axiom, on=off)."
    print(s_axiom)


#groundVersion(4)
#varVersion(4)
#subtermVersion(4)

stdout_backup = sys.stdout

for i in range(1, 21):
    file = "alldiff_switch_gnd%03d.p"%(i)
    with open(file, 'w') as sys.stdout:
        groundVersion(i)
    sys.stdout = stdout_backup

    file = "alldiff_switch_var%03d.p"%(i)
    with open(file, 'w') as sys.stdout:
        varVersion(i)
    sys.stdout = stdout_backup

    file = "alldiff_switch_sub%03d.p"%(i)
    with open(file, 'w') as sys.stdout:
        subtermVersion(i)
    sys.stdout = stdout_backup

for i in range(1, 21):
    file = "onediff_switch_gnd%03d.p"%(i)
    with open(file, 'w') as sys.stdout:
        groundVersion(i, tptpInit2)
    sys.stdout = stdout_backup

    file = "onediff_switch_var%03d.p"%(i)
    with open(file, 'w') as sys.stdout:
        varVersion(i, tptpInit2)
    sys.stdout = stdout_backup

    file = "onediff_switch_sub%03d.p"%(i)
    with open(file, 'w') as sys.stdout:
        subtermVersion(i, tptpInit2)
    sys.stdout = stdout_backup

    



### Solving Towers of Hanoi

This is code for generating the Tower of Hanoi problems from "Planning with Equality".

The state of the game is represented by a term f(x0,....xn), where each of
the variables represents one disk (the biggest disk is represented by x0,
the smallest by xn) and takes one of the values p1, p2, p3 (for "is on peg 1,
peg 2, or peg 3).

In principle, we can generate problems of any size.

In [3]:
def samePegs(peg, n):
    return (",".join([peg]*n))
   
def tptpInitHanoi(n):
    return "cnf(to_plan, negated_conjecture, f(%s)!=f(%s))."%(samePegs("p1", n), samePegs("p2", n))


def distinctPegs():
    return """
cnf(p1neqp2, axiom, p1!=p2).
cnf(p1neqp3, axiom, p1!=p3).
cnf(p2neqp3, axiom, p2!=p3).
    """

def hanoiTerm(n, k, peg1, peg2):
    """
    Create a term of the form f(x0, ..., xk-1, peg1, peg2,...peg2) with a total
    of n arguments.
    """
    args = makeVarlist("X", k)
    args.append(peg1)
    args.extend([peg2]*(n-k-1))
    return "f(%s)"%(",".join(args))

def hanoiAxiom(n, k, peg1, peg2, peg3):
    t1 = hanoiTerm(n, k, peg1, peg3)
    t2 = hanoiTerm(n, k, peg2, peg3)
    return "cnf(h%d_%d%s%s%s, axiom, %s=%s)."%(n,k,peg1,peg2,peg3 , t1, t2)

def hanoiAxiomsPre(n, peg1, peg2, peg3):
    return [hanoiAxiom(n,k,peg1,peg2,peg3) for k in range(n)]

def hanoiAxioms(n):
    """
    Generate all disk-moving axioms for a Tower-of-Hanoi-problem of 
    size n. Since axioms are bidirectional, we only beed half of them.
    """
    res = []
    res.extend(hanoiAxiomsPre(n, "p1", "p2", "p3"))
    res.extend(hanoiAxiomsPre(n, "p1", "p3", "p2"))
    # res.extend(hanoiAxiomsPre(n, "p2", "p1", "p3"))
    res.extend(hanoiAxiomsPre(n, "p2", "p3", "p1"))
    # res.extend(hanoiAxiomsPre(n, "p3", "p1", "p2"))
    # res.extend(hanoiAxiomsPre(n, "p3", "p2", "p1"))
    return res
    
def hanoi(n):
    print("""
%% This is an encoding of the Towers of Hanoi puzzle.
%% There are %d differently sized disks sitting on one of the
%% 3 pegs p1, p2, p3. A bigger disk may never sit on a smaller 
%% disk. One can move the top disk from one peg to another peg
%% if this does nor violate the size constraint.
%% The goal is to move all disks from p1 to p2.
%% 
%% The encoding represents the disks as argument position
%% in a term of the form f(arg1, arg2, ..., argn), where each
%% arg can take the value p1, p2 or p3. The largest disk is on
%% the left, the smallest on the right.
%%
%% There should be 6n=%d axioms (plus inital and goal state), one each
%% to move disk k from any peg to any other peg (for all 6 
%% combinations of two distinct pegs). However, because the axioms
%% are bidirectional, half of them are redundant, so we only need
%% 3n = %d axioms.
"""%(n, 6*n, 3*n))
    print(tptpInitHanoi(n))
    # print(distinctPegs())
    h_axioms = hanoiAxioms(n) 
    print("\n".join(h_axioms))    

# hanoi(1)

stdout_backup = sys.stdout
for i in range(1, 31):
    file = "hanoi_var%03d.p"%(i)
    with open(file, 'w') as sys.stdout:
        hanoi(i)
    sys.stdout = stdout_backup



#### Towers of Hanoi (alternate encoding)

Below is the code for the "variable-free" version encoding the state recusively, and allowing rewriting at subterm positions. In other words, the state is not flat, but recursively encoded.


In [4]:
def wrapPegs(start, peg, n):
    if n==0:
        return start
    else:
        return "f("+peg+","+wrapPegs(start, peg,n-1) +")"

def samePegs2(peg, n):
    return wrapPegs("bot", peg, n)   

def tptpInitHanoi2(n):
    return "cnf(to_plan, negated_conjecture, %s!=%s)."%(samePegs2("p1", n), samePegs2("p2", n))

def hanoiTerm2(n, k, peg1, peg2):
    """
    Create a term of the form f(peg1, f(peg2,...f(peg2, bot))) 
    """
    return wrapPegs(samePegs2(peg2,n-k-1), peg1, 1)


def hanoiAxiom2(n, k, peg1, peg2, peg3):
    t1 = hanoiTerm2(n, k, peg1, peg3)
    t2 = hanoiTerm2(n, k, peg2, peg3)
    return "cnf(h%d_%d%s%s%s, axiom, %s=%s)."%(n,k,peg1,peg2,peg3 , t1, t2)

def hanoiAxiomsPre2(n, peg1, peg2, peg3):
    return [hanoiAxiom2(n,k,peg1,peg2,peg3) for k in range(n)]

def hanoiAxioms2(n):
    """
    Generate all disk-moving axioms for a Tower-of-Hanoi-problem of 
    size n. Since axioms are bidirectional, we only beed half of them.
    """
    res = []
    res.extend(hanoiAxiomsPre2(n, "p1", "p2", "p3"))
    res.extend(hanoiAxiomsPre2(n, "p1", "p3", "p2"))
    # res.extend(hanoiAxiomsPre2(n, "p2", "p1", "p3"))
    res.extend(hanoiAxiomsPre2(n, "p2", "p3", "p1"))
    # res.extend(hanoiAxiomsPre2(n, "p3", "p1", "p2"))
    # res.extend(hanoiAxiomsPre2(n, "p3", "p2", "p1"))
    return res
    
def hanoi2(n):
    print("""
%% This is an encoding of the Towers of Hanoi puzzle.
%% There are %d differently sized disks sitting on one of the
%% 3 pegs p1, p2, p3. A bigger disk may never sit on a smaller 
%% disk. One can move the top disk from one peg to another peg
%% if this does nor violate the size constraint.
%% The goal is to move all disks from p1 to p2.
%% 
%% The encoding represents the disks as argument positions
%% in a term of the form f(arg1, f(arg2, ..., f(argn, bot))), 
%% where each arg can take the value p1, p2 or p3. The largest 
%% disk is on %% the left, the smallest on the right.
%%
%% There should be 6n=%d axioms (plus inital and goal state), one each
%% to move disk k from any peg to any other peg (for all 6 
%% combinations of two distinct pegs). However, because the axioms
%% are bidirectional, half of them are redundant, so we only need
%% 3n = %d axioms.
"""%(n, 6*n, 3*n))
    print(tptpInitHanoi2(n))
    # print(distinctPegs())
    h_axioms = hanoiAxioms2(n) 
    print("\n".join(h_axioms))    

#hanoi2(5)

stdout_backup = sys.stdout
for i in range(1, 31):
    file = "hanoi_sub%03d.p"%(i)
    with open(file, 'w') as sys.stdout:
        hanoi2(i)
    sys.stdout = stdout_backup
